# 1. Setting up of Environment and API Keys

# Install Libraries

In [ ]:
!pip install -q chromadb==0.4.13
!pip install -q langchain==0.0.305
!pip install -q transformers==4.33.3
!pip install -q sentence-transformers==2.2.2
!pip install -q gradio==3.45.2 # not needed for part 1 of article

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 437.8/437.8 kB 7.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.4/2.4 MB 16.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 66.3/66.3 kB 7.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 59.5/59.5 kB 6.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 5.4/5.4 MB 36.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 6.2/6.2 MB 61.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.8/3.8 MB 61.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 67.3/67.3 kB 7.7 MB/s eta 0:00:00
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 593.7/593.7 kB 40.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 67.0/67.0 kB 7.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 46.0/46.0 kB 4.8 M

#Import Libraries

These libraries are needed for web/API scraping, converting scraped text into a vector store to be queried, and for easily loading and querying an LLM.

In [ ]:
# For setting/extracting environment variables such as API keys
import os

### For Web/API Scraping
# for querying Financial Modeling Prep API
from urllib.request import urlopen
import json

### For Converting Scraped Text Into a Vector Store of Chunked Documents
# for tokenizing texts and splitting them into chunks of documents
from transformers import GPT2TokenizerFast
from langchain.text_splitter import RecursiveCharacterTextSplitter
# for turning documents into embeddings before putting them in vector store
from langchain.embeddings import HuggingFaceEmbeddings
# for vector store of document embeddings
from langchain.vectorstores import Chroma

### For Loading LLM and Querying It
# for loading HuggingFace LLM models from the hub
from langchain.llms import HuggingFaceHub
# for querying LLM conveniently using input documents as context
from langchain.chains.question_answering import load_qa_chain

### For Gradio App UI
import gradio as gr # needed for part 2 of the article

## Set up [Financial Modeling Prep API Key](https://utm.io/uf2wb)

This code stores your Financial Modeling Prep API Key in an environment variable and access it when needed.

NOTE: You do not need an API key if you just want to try chatting with earnings call transcripts as I have already scraped recent earnings call transcripts of Tesla with my own API key and put it together with an LLM endpoint into a [gradio app here](https://huggingface.co/spaces/bohmian/chat_with_earnings_call). Feel free to play with it to see how it works!

If you wish to program it yourself, you will need to subscribe for an API Key to be able to scrap stock earnings calls transcripts for any ticker and for any year/quarter using this API. You can sign up for an API key at a discounted rate using [this link](https://utm.io/uf2wb).

NOTE: Instead of subscribing for an API key you can also choose to replace this section of the code with other text scraping code before the next section, where we will call an LLM model, convert the scraped text into a vector database for the user to query upon, and as context for our LLM model to base its answer on.

In [ ]:
os.environ['FMP_API_KEY'] = "your_api_key"
fmp_api_key = os.environ['FMP_API_KEY']

## Set Up HuggingFace API Token

In [ ]:
# Set HuggingFace API Key to load inference endpoint of model
# This API Token must be stored as an environmental variable with this exact name, for HuggingFace API calls to work
os.environ['HUGGINGFACEHUB_API_TOKEN'] = "your_api_key"

# 2. Scrape the Earnings Call Transcripts (Using Financial Modeling Prep API)

This function parses the JSON returned from the Financial Modeling Prep API into a Python dictionary, we will see how we can use it later.

In [ ]:
def get_jsonparsed_data(url):
    response = urlopen(url)
    data = response.read().decode("utf-8")
    return json.loads(data)

Here you can choose to scrape earnings call transcripts for multiple years and multiple tickers by modifying the lists below (each year has up to four quarters of earnings calls). Of course, the more you decide to scrape, the longer it will take especially when covnerting them into a vector database later.

Each transcript is stored as a dictionary that has the following structure:


```
{
    "symbol": "AAPL",
    "quarter": 3,
    "year": 2020,
    "date": "2020-07-30 23:35:04",
    "content": "The content of the call including who is speaking what"
}
```

    
We store all of them into the list called 'transcripts' below.

In [ ]:
# Can choose multiple years, but will take longer time to scrape and convert into vector database
years = [2023]

# Can choose multiple tickers, but will take longer time to scrape and convert into vector database
tickers = ['TSLA']

transcripts = []
for year in years:
    for ticker in tickers:
        url = f"https://financialmodelingprep.com/api/v4/batch_earning_call_transcript/{ticker}?year={year}&apikey={fmp_api_key}"
        transcript = get_jsonparsed_data(url) # this returns a list of dictionaries, each list is a year's worth of earnings calls
        transcripts.extend(transcript) # store all the calls into a single list

# 3. Tokenize the Earnings Calls Transcripts (Using GPT2Tokenizer Fast from HuggingFace) and Split Them Into Multiple Text Chunks (Using RecursiveCharacterTextSplitter from Langchain)

In [ ]:
# Initialize the following text splitter and tokenizer to tokenize and split the texts into chunks later (feel free to try other models)
tokenizer = GPT2TokenizerFast.from_pretrained("gpt2")
# Split into chunks with 200 tokens each, and 20 tokens overlap between successive chunks, feel free to experiment with different parameters
text_splitter = RecursiveCharacterTextSplitter.from_huggingface_tokenizer(tokenizer, chunk_size=200, chunk_overlap=20)

In [ ]:
all_documents = []
for transcript in transcripts:
    # Split each earnings call transcript into document chunks and store it in texts
    documents = text_splitter.create_documents([transcript['content']])
    for document in documents: # The split chunks are called documents
        # Add ticker symbol and date of earnings call to the metadata of each document to easily identify its source in future
        document.metadata = {"title" : f"{transcript['symbol']} Earnings Call: {transcript['date']}"}
    # Add all the documents into document list of all news articles
    all_documents.extend(documents)

Token indices sequence length is longer than the specified maximum sequence length for this model (1499 > 1024). Running this sequence through the model will result in indexing errors


In [ ]:
# Example of a document, note its metadata
all_documents[12]

Document(page_content='Zachary Kirkhorn: Yes. Thanks Martin. As Elon mentioned, Q2 was another record quarter of production and deliveries, as well as records in profit for our energy and services and other businesses. Congratulations again to the Tesla team on the continued progress. As we navigate through a period of economic uncertainty, rising interest rates, volatility in consumer confidence and regulatory change, I want to comment on our financial approach. First, the single most important priority is to ensure we are continuing to invest heavily in the core technologies that will drive the long-term value of the business. This includes increasing spending on AI related technologies such as full self-driving, Optimus and Dojo, as well as new products such as Cybertruck, our next generation platform and the Semi, as evidenced by the continued growth in our R&D spend. This also includes continuing our investments in capacity expansion, not only in our vehicle factories, but also ou

In [ ]:
len(all_documents)

163

#4. Transform the Chunks Into Vector Embeddings (Using HuggingFaceEmbeddings from Langchain) and Store Them in a Vector Store (Using Chroma from Langchain)

In [ ]:
# Initialize the default model for embedding the tokenized texts into vectors so the model can work with them
# The articles will be stored in this vector embeddings in the vector database
hf_embeddings = HuggingFaceEmbeddings()

In [ ]:
persist_directory = 'chromadb_earnings_transcripts'

# Build the vector database using Chroma and persist it in a local directory
# Even after notebook session is restarted, the Chroma db can be loaded from this directory
# Instead of having to scrap the earnings call transcripts and vectorize them all over again
# For this notebook, persisting the database in a directory is optional
chroma_db =  Chroma.from_documents(all_documents,hf_embeddings,persist_directory=persist_directory)
chroma_db.persist()

# 5. Retrieve Chunks of Text Relevant to a User's Query (Using Similarity Search method in Chroma)

In [ ]:
# Search for 4 documents which are closest in meaning to the sample query below and print them out
query = "How is Tesla planning to expand?"
similar_docs = chroma_db.similarity_search(query, k=4)
similar_docs

[Document(page_content="Alex Potter: Okay. Great. And then I guess my second question is on your ability to serve other markets out of Shanghai. Obviously, the facility in Berlin should be opening up your ability to, I guess, allocate more vehicles to Southeast Asia, Australia, other areas. I'm just wondering what other regions do you think you're maybe not yet serving effectively? What are your timelines for addressing some of those gaps in your regional exposure? Thanks.\nElon Musk: Yes. That's a good question because there are still many parts of the world that we do not yet serve with respect to vehicles especially. So we do expect to open up new markets around the world. And while those markets are not necessarily individually gigantic, they do add up to add a whole bunch of markets. They do collectively sum up to something significant. So it's high time that Tesla operates its cars to the rest of the world, and that is something that we intend to do.", metadata={'title': 'TSLA Ea

# 6. Load the LLM (Mistral 7B via HuggingFace Inference Endpoint) and Query the LLM Using the Relevant Chunks of Text as Context (Using Langchain Question Answering)

In [ ]:
# Load the huggingface inference endpoint of an LLM model
# Name of the LLM model we are using, feel free to try others!
model = "mistralai/Mistral-7B-Instruct-v0.1"

# This is an inference endpoint API from huggingface, the model is not run locally, it is run on huggingface
hf_llm = HuggingFaceHub(repo_id=model,model_kwargs={'temperature':0.5,"max_new_tokens":200})

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_deprecation.py:127: FutureWarning: '__init__' (from 'huggingface_hub.inference_api') is deprecated and will be removed from version '0.19.0'. `InferenceApi` client is deprecated in favor of the more feature-complete `InferenceClient`. Check out this guide to learn how to convert your script to use it: https://huggingface.co/docs/huggingface_hub/guides/inference#legacy-inferenceapi-client.
  warnings.warn(warning_message, FutureWarning)


In [ ]:
# Query the LLM using the similar docs as context
qa_chain = load_qa_chain(hf_llm, chain_type="stuff",verbose=True) # Use True for verbose, to output what is being given to the model in full
qa_chain.run(input_documents=similar_docs, question=f"[INST]{query}[/INST]")



> Entering new StuffDocumentsChain chain...


> Entering new LLMChain chain...
Prompt after formatting:
Use the following pieces of context to answer the question at the end. If you don't know the answer, just say that you don't know, don't try to make up an answer.

Alex Potter: Okay. Great. And then I guess my second question is on your ability to serve other markets out of Shanghai. Obviously, the facility in Berlin should be opening up your ability to, I guess, allocate more vehicles to Southeast Asia, Australia, other areas. I'm just wondering what other regions do you think you're maybe not yet serving effectively? What are your timelines for addressing some of those gaps in your regional exposure? Thanks.
Elon Musk: Yes. That's a good question because there are still many parts of the world that we do not yet serve with respect to vehicles especially. So we do expect to open up new markets around the world. And while those markets are not necessarily individually gigantic, the

'\n\nTesla is planning to expand its operations in various ways. One way is by opening new markets around the world, especially in regions that do not yet have Tesla vehicles available. They intend to invest heavily into their future plans, which include the Cybertruck, in-house cell production, energy storage, and autonomy and AI-enabled products. Additionally, they plan to continue to grow their volumes as quickly as possible in both their vehicle and energy businesses, while keeping the business financially healthy and industry leading. To accomplish this, they need to remain focused on cost efficiency and working capital and unwind the strategic inventory buildup left over from the pandemic.'

## 6.1. Combine the above into a convenient function

In [ ]:
def qa_compute(query:str,vectorstore:Chroma,llm:HuggingFaceHub,verbose=False):
  """
  Print all the simuilar docs and return answer to the query
  """
  similar_docs = vectorstore.similarity_search(query,k=4)
  qa_chain = load_qa_chain(llm, chain_type="stuff",verbose=verbose)
  response = qa_chain.run(input_documents=similar_docs, question=f"[INST]{query}[/INST]")

  return response, similar_docs

## 6.2. Ask a Few More Questions!

In [ ]:
query = "What are the challanges faced by Tesla and how did the affect earnings?"
qa_compute(query,chroma_db,hf_llm)

("\n\nDuring Q1 2023, Tesla faced several challenges that affected its earnings. One of the main challenges was the impact of additional action taken in the second half of the quarter to improve vehicle pricing. This, combined with one-time items such as warranty adjustments on older S and X vehicles and increased deferred revenue for certain Autopilot features, led to a reduction in automotive gross margin and operating margin.\n\nAnother challenge faced by Tesla was the macro environment, which remained uncertain, particularly with large purchases such as cars. Despite reducing prices considerably in early Q1, the operating margin remained among the best in the industry.\n\nDespite these challenges, Tesla's team was able to achieve record vehicle production and deliveries, and the energy storage team also set a record for volumes. The company's progress on vehicle cost reduction continued in Q1 with meaningful improvements on logistics and the beginnings of some commodity cost",
 [Do

In [ ]:
query = "Is Tesla coping well with its challenges?"
qa_compute(query,chroma_db,hf_llm)

(" Based on the information provided in the context, it seems that Tesla is facing challenges in production and delivery of its vehicles, but despite these challenges, the company has achieved significant success in sales of Model Y in Europe and the United States. The company has also made progress on storage profitability and is investing heavily in its future plans. The company's approach is to grow volumes as quickly as possible in both its vehicle and energy businesses while keeping the business financially healthy and industry leading.",
 [Document(page_content="Elon Musk: Thank you, Martin. So just a Q1 recap. Model Y became the best-selling vehicle of any kind in Europe and the best-selling non-pickup vehicle in the United States. And this is in spite of a lot of challenges in production and delivery. So it's a huge credit to the Tesla team for achieving these great results. The -- it is worth pointing out that the current macro environment remains uncertain. I don't think I'm 

In [ ]:
query = "Is Elon happy about Tesla?"
qa_compute(query,chroma_db,hf_llm)

(" Yes, based on the context provided, it appears that Elon Musk is happy about Tesla. He mentions several achievements of the company, including being the best-selling vehicle of any kind in Europe and the United States, and achieving record vehicle production and deliveries and record revenue in Q2. He also mentions Tesla's continued target of 1.8 million vehicle deliveries this year, despite a slight decrease in production due to summer shutdowns.",
 [Document(page_content="Elon Musk: Thank you, Martin. So just a Q1 recap. Model Y became the best-selling vehicle of any kind in Europe and the best-selling non-pickup vehicle in the United States. And this is in spite of a lot of challenges in production and delivery. So it's a huge credit to the Tesla team for achieving these great results. The -- it is worth pointing out that the current macro environment remains uncertain. I don't think I'm telling anyone anything, I think people already know, especially with large purchases such as